In [1]:
import pandas as pd
import numpy as np

import plotly.graph_objects as go
import plotly.express as px

In [2]:
dataset_url = r'https://raw.githubusercontent.com/miptgirl/kinopoisk_data/master/kp_all_movies.csv'
dataframe = pd.read_csv(dataset_url)
dataframe = dataframe[['movie_id', 'imdb_rating']].dropna()

In [3]:
def get_class(rating):
    if rating >= 7:
        return 'Positive'
    elif rating <= 4: 
        return 'Negative'
    else:
        return 'Neutral'

dataframe["class"] = dataframe.loc[:, "imdb_rating"].apply(get_class)
dataframe["imdb_rating_10"] = dataframe.loc[:, "imdb_rating"].apply(lambda a: round(a, 1))
fig = px.histogram(dataframe, x="imdb_rating", color="class", color_discrete_sequence=["#00cc96", "#4C78A8", "#EF553B"])#), histnorm='probability')
fig.show()

In [4]:
fig = px.histogram(dataframe, x="class", histnorm='probability')
fig.show()

In [5]:
#Получение пограничных значений
length = len(dataframe)

classes = ['Negative', 'Neutral', 'Positive']
values = [len(dataframe[dataframe['class'] == cls]) / length for cls in classes]
acc_values = np.cumsum(values)
acc_values

array([0.05780085, 0.62065739, 1.        ])

Получение распределения негативных, нейтральных и позитивных оценок, на основе предиктов классификатора.

In [6]:
def get_rating(p):
    if p < acc_values[2]:
        val = 'Positive'
    if p < acc_values[1]:
        val = 'Neutral'
    if p < acc_values[0]:
        val = 'Negative'
    return val
    
predictions = pd.read_csv('Predictions_final.csv')
predictions["class"] = predictions.loc[:, "Score"].apply(get_rating)
fig = px.histogram(predictions, x="Score", color="class", color_discrete_sequence=["#00cc96", "#4C78A8", "#EF553B"])
fig.show()  

Создание "Промежуточного" распределения

In [7]:
def get_normalized_score(p):
    if p <= acc_values[2]:
        val = ((p - acc_values[1]) / (1 - acc_values[1])) * 3 + 7
    if p <= acc_values[1]:
        val = ((p - acc_values[0]) / (acc_values[1] - acc_values[0])) * 3 + 4
    if p <= acc_values[0]:
        val = ((p - 0) / (acc_values[0] - 0)) * 4 + 0
    return val

predictions["nscore"] = predictions.loc[:, "Score"].apply(get_normalized_score)
predictions["nscore_10"] = predictions.loc[:, "nscore"].apply(lambda a: round(a))
fig = px.histogram(predictions, x="nscore", color="class", color_discrete_sequence=["#00cc96", "#4C78A8", "#EF553B"])
fig.show() #Теперь сделаем перевод

In [8]:
from modules.dist_map import DistributionMap

X = predictions.loc[:, "nscore"]
Y = dataframe.loc[:, "imdb_rating"]

dist_map = DistributionMap(X / 10, Y / 10, n_bins=10)


fig = px.line(x=np.linspace(0, 1, 20000), y=np.round(dist_map(np.linspace(0, 1, 20000)), 2))

fig.show()

#Теперь распределения больше похоже на правду: Большинство оценок от 5 до 6, и минимальное количество оценок 1-3 и 8-10.

In [9]:
from modules.dist_map import DistributionMap
import pickle

with open('./models/rating.pkl', 'wb') as f:
    pickle.dump(dist_map, f)

    